In [1]:
import django
import os
import pandas as pd
import numpy as np
import html
import namedentities as ne
from old_database.modules_webpage import entry_to_dict #read_publications, read_addresses, read_seminars
import time

os.environ.setdefault("DJANGO_SETTINGS_MODULE", "nanotud.settings")
from django.core.wsgi import get_wsgi_application
application = get_wsgi_application()
#from research.models import Publication


#from home.models import Room, Country, Title_full, Gender, Status
#from internal.models import Member
from external.models import Event
#from teaching.models import Seminar

# needed when run inter jupyter enviornment:
os.environ["DJANGO_ALLOW_ASYNC_UNSAFE"] = "true"
django.setup()

#import gender_guesser.detector as gender
import re


## Write old papers database

In [2]:
def read_addresses(file_name):
    
    with open(file_name, 'r') as file:
            content = file.read() 
    all_entries = content.split('enditem')
    
    for entry in all_entries:
        dictio = entry_to_dict(entry)
        if dictio != {}:
            try:
                df = df.append(dictio, ignore_index=True)     # append new entry to DF
            except:
                df = pd.DataFrame(dictio, index=[0])          # first time create the DF
    df = df.fillna(np.NaN)
    #ind = df[df['vorname'].isna() & df['nachname'].isna()].index.values
    #df.drop(ind,inplace=True)
    return df

In [3]:
path_events = 'old_database/database.events'
df_events = read_addresses(path_events)

# take only publications with DOI
#df_papers = df_papers[~df_papers['DOI'].isnull()]

# only publications with reference
#df_papers = df_papers[~df_papers['reference'].isnull()]
# df_papers = df_papers[~(df_papers['type']=='inbook')]

In [4]:
df_events

conforg                  conflogo deadyear deadmonth deadday  \
0       yes          grapheneconf2021     2021        04      12   
1       yes                logo_codec     2019        07      01   
2       yes                      icsm     2022        01      01   
3       yes                  I3S-2020     2020        12      28   
4       yes                  logo_MSE     2020        12      28   
..      ...                       ...      ...       ...     ...   
599     NaN                       NaN     2003        02      15   
600     NaN                       NaN     2003        01      17   
601     NaN                       NaN     2002        11      30   
602     yes         2002_09_Rome_NN02     2002        05      15   
603     yes  2001_02_Dresden_transmol     2001        01      21   

                                            organizers  year month   days  \
0    J.-C. Charlier, A. Correira, Fr. Bonaccorso, X...  2021    10  26-29   
1                S. C. Banerjee, A. Das Barman, G. Sen  2019    12  19-20   
2                                 K. Leo, G. Cuniberti  2022    07  03-08   
3             Luigi Zeni, Nunzio Cennamo, Aldo Minardo  2020    06  03-05   
4                     Gianaurelio Cuniberti, Hong Wang  2020    09     24   
..                                                 ...   ...   ...    ...   
599                J. Ankerhold, P. Reimann, T. Geisel  2003    05  20-24   
600                                     R. H&ouml;lzle  2003    03  10-21   
601                H. Bouchiat, M. Di Ventra, P. Weiss  2003    04  21-25   
602                       S. Bellucci, M. De Crescenzi  2002    09  23-28   
603                 G. Cuniberti, G. Fagas, K. Richter  2001    02  23-24   

                                         conferenceref  \
0           http://www.grapheneconf.com/2021/index.php   
1                            http://www.codec-rpe.org/   
2                              http://www.icsm2022.com   
3       https://sciforum.net/conference/i3s2020Dresden   
4                                                        
..                                                 ...   
599                    http://www.pks.mpg.de/~batco03/   
600         http://www.fz-juelich.de/iff/ferienschule/   
601  http://www.mrs.org/meetings/spring2003/cfp/k.html   
602          http://www.lnf.infn.it/conference/nn2002/   
603                   http://www.pks.mpg.de/~transmol/   

                                              whereref  \
0                                                  NaN   
1                                                  NaN   
2                                                  NaN   
3                                                        
4                                                        
..                                                 ...   
599  http://www.pks.mpg.de/mpi-doc/fuldegruppe/inst...   
600                      http://www.fz-juelich.de/iff/   
601  http://directory.google.com/Top/Regional/North...   
602                       http://www.villamercede.com/   
603  http://www.pks.mpg.de/mpi-doc/fuldegruppe/inst...   

                       where  \
0           Grenoble, France   
1             Kolkata, India   
2           Dresden, Germany   
3           Dresden, Germany   
4                     Online   
..                       ...   
599         Dresden, Germany   
600     J&uuml;lich, Germany   
601       San Francisco, USA   
602  Frascati by Rome, Italy   
603         Dresden, Germany   

                                            conference  \
0                                        Graphene 2021   
1    International Conference on Computers and devi...   
2    International Conference on Science and Techno...   
3    I3S - 8th International Symposium on Sensor Sc...   
4    DGM Symposium &quot;Materials Genome Engineeri...   
..                                                 ...   
599  International Workshop: Classical and quantum ...   
600  4th IFF Spring

In [5]:
df_events.columns

Index(['conforg', 'conflogo', 'deadyear', 'deadmonth', 'deadday', 'organizers',
       'year', 'month', 'days', 'conferenceref', 'whereref', 'where',
       'conference', 'abstract', 'The', '', 'school', 'registrationref'],
      dtype='object')

**Write to Django Database**

In [6]:
for index, row in df_events.iterrows():
    dyear_start_raw=None
    dmonth_start_raw=None
    dday_start_raw=None
    if type(row['deadyear']) != float: # or row['deadyear']!='' :
        dyear_raw=row['deadyear']
        dyear_list=dyear_raw.split('-')
        dyear_start_raw=dyear_list[0]
        dyear_end_raw=dyear_list[-1]
        try:
            int(dyear_start_raw)
        except:
            dyear_start_raw=None
        print(dyear_start_raw)
    else:
        dyear=None
    if type(row['deadmonth']) !=float: # or row['deadmonth']!='':
        dmonth_raw=row['deadmonth']
        dmonth_list=dmonth_raw.split('-')
        dmonth_start_raw=dmonth_list[0]
        dmonth_end_raw=dmonth_list[-1]
    else:
        dmonth_start_raw='01'
        dmonth_end_raw='01'
    if type(row['deadday'])!= float: #or row['deadday']!='':
        dday_raw=row['deadday']
        dday_list=dday_raw.split('-')
        dday_start_raw=dday_list[0]
        dday_end_raw=dday_list[-1]
    else:
        dday_start_raw='01'
        dday_end_raw='01'
    dhour='08:00'
    
    if type(row['year'])!= float: # or row['year']!='':
        year_raw=row['year']
        year_list=year_raw.split('-')
        year_start_raw=year_list[0]
        year_end_raw=year_list[-1]
    else:
        year_raw=None
    if type(row['month'])!=float: # or row['month']!='':
        month_raw=row['month']
        month_list=month_raw.split('-')
        month_start_raw=month_list[0]
        month_end_raw=month_list[-1]  
    else:
        month_start_raw='01'
        month_end_raw='01'
    if type(row['days'])!=float: # or row['days']!='':
        day_raw=row['days']
        day_list=day_raw.split('-')
        print('yes',day_list)
        day_start_raw=day_list[0]
        day_end_raw=day_list[-1]
    else:
        day_start_raw='01'
        day_end_raw='01'
    hour='08:00'
    public_raw=False
    if type(row['organizers'])!=float:
        organizers_raw=row['organizers']
    else:
        organizers_raw=None
    if row['conforg']=='yes':
        conforg_raw=True
        public_raw=True
    else:
        conforg_raw=False
        public_raw=False   
    title_raw = html.unescape(row['conference'])
    if type(row['where'])!=float:
        where_raw=row['where']
    else:
        where_raw=None
    if type(row['whereref'])!=float:
        whereref_raw=row['whereref']
    else:
        whereref_raw=None
    try:
        abstract_raw= row['abstract']
    except:
        abstract_raw = None
    if type(row['conferenceref'])!=float:
        conferenceref_raw=row['conferenceref']
    else:
        conferenceref_raw=None
    if row['conflogo']!='' and type(row['conflogo'])!=float:
        for ending in os.listdir('uploads/events/logo/'):
            if row['conflogo']+'.jpg' == ending:
                conflogo_raw='uploads/events/logo/' + row['conflogo']+'.jpg'
            if row['conflogo']+'.gif' == ending:
                conflogo_raw='uploads/events/logo/' + row['conflogo']+'.gif'
            if row['conflogo']+'.png' == ending:
                conflogo_raw='uploads/events/logo/' + row['conflogo']+'.png'
    startTime_raw = f"{year_start_raw}-{month_start_raw}-{day_start_raw} {hour}"
    endTime_raw = f"{year_end_raw}-{month_end_raw}-{day_end_raw} {hour}"
    if dyear_start_raw!=None:
        registrationDeadline_raw = f"{dyear_start_raw}-{dmonth_start_raw}-{dday_start_raw} {dhour}"
    else:
        registrationDeadline_raw=None
    print('daystart_raw',day_start_raw)
    print('monthstart_raw',month_start_raw)
    print('ddaystart_raw',type(dday_start_raw),row['deadday'])
    print('dmonthstart_raw',type(dmonth_start_raw),row['deadmonth'])
    print(title_raw)
    if type(row['abstract'])==float: abstract_raw=''
    new_event = Event(  title=title_raw,
                          description=abstract_raw,
                          startTime=startTime_raw,
                          endTime=endTime_raw,
                          registrationDeadline=registrationDeadline_raw,
                          image=conflogo_raw,
                          selfOrganized=conforg_raw,
                          public=public_raw,
                          externalLink=conferenceref_raw,
                          location=where_raw,
                          externalLocation=whereref_raw,
                          organizers=organizers_raw,
                        )
    new_event.save()
    time.sleep(0.25)

2021
yes ['26', '29']
daystart_raw 26
monthstart_raw 10
ddaystart_raw <class 'str'> 12
dmonthstart_raw <class 'str'> 04
Graphene 2021


/home/service/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Event.startTime received a naive datetime (2021-10-26 08:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/home/service/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Event.endTime received a naive datetime (2021-10-29 08:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/home/service/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Event.registrationDeadline received a naive datetime (2021-04-12 08:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"


2019
yes ['19', '20']
daystart_raw 19
monthstart_raw 12
ddaystart_raw <class 'str'> 01
dmonthstart_raw <class 'str'> 07
International Conference on Computers and devices for Communication (CODEC)


/home/service/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Event.startTime received a naive datetime (2019-12-19 08:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/home/service/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Event.endTime received a naive datetime (2019-12-20 08:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/home/service/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Event.registrationDeadline received a naive datetime (2019-07-01 08:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"


2022
yes ['03', '08']
daystart_raw 03
monthstart_raw 07
ddaystart_raw <class 'str'> 01
dmonthstart_raw <class 'str'> 01
International Conference on Science and Technology of Synthetic Metals (ICSM) 2022


...

/home/service/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Event.startTime received a naive datetime (2003-04-21 08:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/home/service/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Event.endTime received a naive datetime (2003-04-25 08:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/home/service/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Event.registrationDeadline received a naive datetime (2002-11-30 08:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"


2002
yes ['23', '28']
daystart_raw 23
monthstart_raw 09
ddaystart_raw <class 'str'> 15
dmonthstart_raw <class 'str'> 05
Nanotubes & Nanostructures 2002


/home/service/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Event.startTime received a naive datetime (2002-09-23 08:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/home/service/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Event.endTime received a naive datetime (2002-09-28 08:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/home/service/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Event.registrationDeadline received a naive datetime (2002-05-15 08:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"


2001
yes ['23', '24']
daystart_raw 23
monthstart_raw 02
ddaystart_raw <class 'str'> 21
dmonthstart_raw <class 'str'> 01
Electron Transport on the Molecular Scale (transmol)


/home/service/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Event.startTime received a naive datetime (2001-02-23 08:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/home/service/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Event.endTime received a naive datetime (2001-02-24 08:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/home/service/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Event.registrationDeadline received a naive datetime (2001-01-21 08:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"


Old stuff:

In [ ]:
int('    ')